In [ ]:
! pip install seaborn

In [ ]:
! pip install Plotly

In [ ]:
! pip install nbformat==4.2.0

In [ ]:
! pip install --upgrade nbformat

In [43]:
import pandas as pd
import seaborn as sns
import plotly.express as px
from plotly.subplots import make_subplots
import sqlite3

In [6]:
con = sqlite3.Connection("../data/energi.sqlite")

In [7]:
# extract data from CO2Emis and also aggregate the HourUTC using SQL
# strip the data of '2022-12-31 23:00:00' due to the time difference between UTC and in denmark, the fetched data from 2023.01.01 included data of last hour of 2022-12-31
CO2_Emission = pd.read_sql_query(
    """
SELECT 
    STRFTIME("%d-%m-%Y %H:00:00", Minutes5UTC) as HourUTC,
    sum(CO2Emission) as CO2Emission,
    PriceArea
FROM CO2Emis
WHERE Minutes5UTC >= '2023-01-01 00:00:00'
GROUP BY Minutes5UTC
""",
    con,
)
CO2_Emission["HourUTC"] = pd.to_datetime(
    CO2_Emission["HourUTC"], format="%d-%m-%Y %H:00:00"
)

In [8]:
# extract data from DeclarationGridMix and also aggregate the data by report group as well as strip the data by only focusing on DK1 price area
gridmix = pd.read_sql_query(
    """
SELECT 
    HourUTC, 
    ReportGrp, 
    sum(SharePPM) as SharePPM, 
    sum(ShareMWh) as ShareMWh, 
    sum(CO2Emission) as CO2Emission 
FROM DeclarationGridMix
WHERE PriceArea = "DK1" AND HourUTC >= '2023-01-01 00:00:00'
GROUP BY ReportGrp, HourUTC;
""",
    con,
)
gridmix["HourUTC"] = pd.to_datetime(gridmix["HourUTC"])

In [11]:
production = pd.read_sql_query(
    "SELECT * FROM DeclarationProduction", con, parse_dates=["HourUTC"]
)

In [9]:
CO2_Emission.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 101352 entries, 0 to 101351
Data columns (total 3 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   HourUTC      101352 non-null  datetime64[ns]
 1   CO2Emission  101352 non-null  float64       
 2   PriceArea    101352 non-null  object        
dtypes: datetime64[ns](1), float64(1), object(1)
memory usage: 2.3+ MB


In [10]:
gridmix.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 133877 entries, 0 to 133876
Data columns (total 5 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   HourUTC      133877 non-null  datetime64[ns]
 1   ReportGrp    133877 non-null  object        
 2   SharePPM     133877 non-null  int64         
 3   ShareMWh     133877 non-null  float64       
 4   CO2Emission  110167 non-null  float64       
dtypes: datetime64[ns](1), float64(2), int64(1), object(1)
memory usage: 5.1+ MB


In [40]:
production.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 429364 entries, 0 to 429363
Data columns (total 27 columns):
 #   Column                Non-Null Count   Dtype         
---  ------                --------------   -----         
 0   HourUTC               429364 non-null  datetime64[ns]
 1   HourDK                429364 non-null  object        
 2   PriceArea             429364 non-null  object        
 3   Version               429364 non-null  object        
 4   FuelAllocationMethod  429364 non-null  object        
 5   ReportGrpCode         429364 non-null  object        
 6   ProductionType        429364 non-null  object        
 7   DeliveryType          429364 non-null  object        
 8   Production_MWh        429364 non-null  float64       
 9   ShareTotal            429364 non-null  float64       
 10  ShareGrid             429364 non-null  float64       
 11  FuelConsumptionGJ     429364 non-null  float64       
 12  CO2PerkWh             429364 non-null  float64       
 13 

Explore the dataset CO2Emission

In [12]:
# add Hour, Day, Month and Date columns to the CO2_Emission dataframe
CO2_Emission["Date"] = CO2_Emission["HourUTC"].dt.date
CO2_Emission["Month"] = CO2_Emission["HourUTC"].dt.month
CO2_Emission["Day"] = CO2_Emission["HourUTC"].dt.day
CO2_Emission["Hour"] = CO2_Emission["HourUTC"].dt.hour

In [13]:
CO2_Emission.head()

HourUTC  CO2Emission PriceArea        Date  Month  Day  Hour
0 2023-01-01        336.0       DK1  2023-01-01      1    1     0
1 2023-01-01        320.0       DK1  2023-01-01      1    1     0
2 2023-01-01        310.0       DK1  2023-01-01      1    1     0
3 2023-01-01        304.0       DK1  2023-01-01      1    1     0
4 2023-01-01        290.0       DK1  2023-01-01      1    1     0

In [37]:
# 1.Explore the CO2 Emission overtime in different timeframe,like in a day, in a month.
timeframe_to_plot = ["Hour", "Day"]

mean_CO2_Emission_by_timeframe = CO2_Emission.groupby(timeframe_to_plot)[
    "CO2Emission"
].mean()
fig = make_subplots(
    rows=1,
    cols=2,
    subplot_titles=[
        "CO2 Emission in a day",
        "CO2 Emission in a month",
    ],
)

for i, timeframe in enumerate(timeframe_to_plot, 1):
    trace = px.box( 
        CO2_Emission,
        x=timeframe,
        y="CO2Emission",
        points= "all",
        title=f"CO2 Emission in {timeframe}",
    )
    fig.add_trace(trace.data[0], row=1, col=i)
fig.update_xaxes(title_text=timeframe_to_plot[0], row=1, col=1)
fig.update_xaxes(title_text=timeframe_to_plot[1], row=1, col=2)
fig.update_yaxes(title_text="CO2 Emission", row=1, col=1)
fig.update_yaxes(title_text="", row=1, col=2) 

fig.update_layout(
    title_text="CO2 Emission Over Time in different timeframe",
    title_x=0.5,
    showlegend=False,
)
fig.show()

In [47]:
# 2. explore the CO2 Emission changes during the 2023.01.01-2023.12.18

CO2_Hourly = CO2_Emission.groupby("Date")["CO2Emission"].sum().reset_index()
fig = px.line(CO2_Hourly, x="Date", y="CO2Emission")
fig.update_layout(
    title="CO2 Emission over time",
    xaxis_title="Time",
    yaxis_title="CO2 Emission",
    title_x=0.5,
    showlegend=True,
)
fig.show()

Exploring the dataset DeclarationGridMix

In [15]:
gridmix.head()

HourUTC ReportGrp  SharePPM   ShareMWh  CO2Emission
0 2023-01-01 00:00:00    BioGas     10921  50.435916          0.0
1 2023-01-01 01:00:00    BioGas     10101  49.318108          0.0
2 2023-01-01 02:00:00    BioGas     10216  47.656042          0.0
3 2023-01-01 03:00:00    BioGas     10464  47.637956          0.0
4 2023-01-01 04:00:00    BioGas     11075  49.126596          0.0

In [16]:
# 3. exlpore the sum of CO2 Emissions during 2023 by different report group in price Area DK1
# strip the NaN as well as the report group like solar which produce no CO2 emissions
CO2_grid = gridmix.groupby("ReportGrp")["CO2Emission"].sum().reset_index()
CO2_grid = CO2_grid.dropna()
CO2_Group = CO2_grid[CO2_grid["CO2Emission"] > 0]

In [39]:
CO2_Group = CO2_Group.sort_values(by="CO2Emission", ascending=True)
fig = px.bar(
    CO2_Group,
    y="ReportGrp",
    x="CO2Emission",
    title="CO2 Emission by different report group in DK1",
)
fig.update_layout(title_x=0.5, showlegend=True)
fig.show()

Explore the dataset DeclarationProduction

In [41]:
production.head()

HourUTC               HourDK PriceArea      Version  \
0 2023-01-01 22:00:00  2023-01-01 23:00:00       DK1  Preliminary   
1 2023-01-01 22:00:00  2023-01-01 23:00:00       DK1  Preliminary   
2 2023-01-01 22:00:00  2023-01-01 23:00:00       DK1  Preliminary   
3 2023-01-01 22:00:00  2023-01-01 23:00:00       DK1  Preliminary   
4 2023-01-01 22:00:00  2023-01-01 23:00:00       DK1  Preliminary   

  FuelAllocationMethod ReportGrpCode ProductionType DeliveryType  \
0                 125%         R01-1         BioGas         Grid   
1                 125%         R01-2          Straw         Grid   
2                 125%         R01-3           Wood         Grid   
3                 125%          R04x      FossilGas         Grid   
4                 125%          R05x           Coal         Grid   

   Production_MWh  ShareTotal  ...    CH4PerkWh     COPerkWh  N2OPerkWh  \
0       54.002268    2.063986  ...  2656.993606  1898.507178   9.797154   
1       36.396839    1.391100  ...     3.163771   451.005779   7.404572   
2       94.664896    3.618127  ...    26.329985   736.547643   7.202707   
3       25.837461    0.987517  ...   224.123413    94.985808   6.318167   
4      163.688322    6.256229  ...     7.454567    82.828522   6.626281   

   SlagPerkWh  FlyAshPerkWh  ParticlesPerkWh  WastePerkWh  DesulpPerkWh  \
0    0.000000      0.000000        16.128851          0.0      0.000000   
1    6.071749      2.625257        15.482287          0.0      0.000000   
2    6.853838      2.963411       122.697627          0.0      0.000000   
3    0.000000      0.000000        27.792778          0.0      0.000000   
4    6.410927     37.247986        24.848556          0.0     13.542463   

         date  Hour  
0  2023-01-01    22  
1  2023-01-01    22  
2  2023-01-01    22  
3  2023-01-01    22  
4  2023-01-01    22  

[5 rows x 27 columns]

In [48]:
production['PriceArea'].value_counts()

PriceArea
DK1    214682
DK2    214682
Name: count, dtype: int64

In [58]:
# 4. explore the sum of electricity production by different report group in 2023
production_type = (
    production.groupby(["ProductionType","PriceArea"])["Production_MWh"]
    .sum()
    .reset_index()
    .sort_values(by="Production_MWh")
)
fig = px.bar(
    production_type,
    y="ProductionType",
    x="Production_MWh",
    color="PriceArea",
    title="Electricity Production by Type",
)
fig.update_layout(title_x=0.5, showlegend=True)
fig.show()

In [21]:
# 5. explore the sum of electricity production by different report group in different hour of the day
# As it shows that during during the daytime the solar produce more electricity than during the dark
production["Hour"] = production["HourUTC"].dt.hour
production_hour = (
    production.groupby(["Hour", "ProductionType"])["Production_MWh"].sum().reset_index()
)

In [22]:
fig = px.bar(
    production_hour,
    x="Hour",
    y="Production_MWh",
    color="ProductionType",
    title="Electricity Production by report group during a day",
)
fig.update_layout(xaxis_title="hour of the day", title_x=0.5, showlegend=True)
fig.show()

In [56]:
#6. explore fuel consumption in different price area
fuel_consumption=production.groupby(['PriceArea','ProductionType'])['FuelConsumptionGJ'].sum().reset_index()
px.line(fuel_consumption, x='ProductionType',y='FuelConsumptionGJ', color='PriceArea', markers=True, title='Fuel Comsumption by Production Type')